In [1]:
import pycorrector
import os
import math
import pandas as pd
import jieba
import utils
import numpy as np
import heapq
from collections import Counter

In [2]:
#step 1 创建BM25模型
class BM25(object):
  def __init__(self,docs,raw):
    self.test_times = 531
    self.top1 = 382
    self.top5 = 455                   #截止至6月29号，其中前200次是原文复制粘贴，后300次是自己输入的搜索内容
    self.docs = docs   # 传入的docs要求是已经分好词的list 
    self.titles = raw[0]    # 文章标题
    self.raw_docs = raw[1]   #文章原文，方便查看
    self.doc_num = len(docs) # 文档数
    self.vocab = set([word for doc in self.docs for word in doc]) # 文档中所包含的所有词语
    self.avgdl = sum([len(doc) + 0.0 for doc in docs]) / self.doc_num # 所有文档的平均长度
    self.k1 = 1.5
    self.b = 0.75
    self.f = []  # 列表的每一个元素是一个dict，dict存储着一个文档中每个词的出现次数
    self.df = {} # 存储每个词及出现了该词的文档数量
    self.idf = {} # 存储每个词的idf值
    self.init()
                
  def cal(self,start,end):
    for index in range(start,end):
        doc = self.docs[index]
        tmp = {}
        for word in doc:
            tmp[word] = tmp.get(word, 0) + 1  # 存储每个文档中每个词的出现次数
        self.f.append(tmp)
        for k in tmp.keys():
            self.df[k] = self.df.get(k, 0) + 1
    for k, v in self.df.items():
        self.idf[k] = math.log(self.doc_num-v+0.5)-math.log(v+0.5)
        
  def init(self):
    self.cal(0,len(self.docs))

  def add_new(self,docs,raw): #再次添加新的文章时使用
    start = self.doc_num
    self.docs = self.docs + docs
    self.titles = self.titles + raw[0]
    self.raw_docs = self.raw_docs + raw[1]
    self.doc_num += len(docs)
    end = self.doc_num
    self.cal(start,end)

  def score(self,word):
    score_list = []
    
    for index,doc in enumerate(self.docs):
      word_count = self.f[index]  #本文章中各个词的词频(dict形式)
      if word in word_count.keys():
        f = (word_count[word]+0.0) / len(doc) #注意区分词的出现频率与出现次数
      else:
        f = 0.0 
      r_score = (f*(self.k1+1)) / (f+self.k1*(1-self.b+self.b*len(doc)/self.avgdl))
      score_list.append(self.idf.get(word,0) * r_score)
    return score_list 

  def score_all(self,sequence):
    sum_score = []
    for word in sequence:
        sum_score.append(self.score(word))
        #print(word,self.score(word))
    #print(sum_score)
    sim = np.sum(sum_score,axis=0)
    #print(np.array(sim))
    return sim


In [3]:
#step 2 获取停用词
stopwords_path = './stopwords.txt'
stopwords = open(stopwords_path,encoding = "utf-8").read().split('\n')

#获取同义词
synonym_path = './同义词库.txt'
synonym_path = open(synonym_path,encoding = "utf-8").read().split('\n')

In [4]:
#step 3 读取excel中数据
def read_xl(excel_path):
    data1 = pd.read_excel(excel_path,sheet_name = 0,usecols = [7])
    data2 = pd.read_excel(excel_path,sheet_name = 0,usecols = [0])
    height,width= data1.shape
    titles = []
    texts = []
    for i in range(height):
        texts.append(data1.iloc[i,0])
        titles.append(data2.iloc[i,0])
    return titles,texts

In [5]:
#step 4 创建一个BM25实例
titles,texts = read_xl("test.xlsx")
docs = []
raw = []
for text in texts:
    doc_list = [doc for doc in str(text).split('\n') if doc != '']
    new_text = "".join(doc_list)
    raw.append(new_text)
    words = jieba.lcut(new_text)
    tokens = []
    for word in words:
        if word in stopwords:
            continue
        else:
            tokens.append(word)
    docs.append(tokens)        
bm = BM25(docs,[titles,raw])



In [6]:
#当然语料不一定在一个表格中，其他的excel储存在doc文件夹下
#对这些表格进行读取
paths = os.listdir("./docs/")
for path in paths:
    titles,texts = read_xl("./docs/" + path)
    docs = []
    raw = []
    for text in texts:
        doc_list = [doc for doc in str(text).split('\n') if doc != '']
        new_text = "".join(doc_list)
        raw.append(new_text)
        words = jieba.lcut(new_text)
        tokens = []
        for word in words:
            if word in stopwords:
                continue
            else:
                tokens.append(word)
        docs.append(tokens)
    bm.add_new(docs,[titles,raw])

In [7]:
bm.f #列表的每一个元素是一个dict，dict存储着一个文档中每个词的出现次数

[{'前段时间': 1,
  '小伙': 1,
  '花': 1,
  '数万': 1,
  '块': 1,
  '买条': 1,
  '怪鱼': 1,
  '一刀切': 1,
  '开': 1,
  '愣住': 1,
  '鱼肉': 3,
  '蓝色': 2,
  '吃': 2,
  '少见': 1,
  '却是': 1,
  '食用': 1,
  '味道': 1,
  '鱼生': 1,
  '发现': 1,
  '鱼': 1,
  '肉': 1,
  '颜色': 2,
  '粉色': 1,
  '红色': 1,
  '深红色': 1,
  '白色': 1,
  '口感': 1,
  '相差': 1},
 {'小编': 4,
  '没到': 1,
  '老婆': 1,
  '孩子': 1,
  '跳': 1,
  '爱': 1,
  '年龄': 1,
  '梦华': 1,
  '录': 1,
  '流泪': 1,
  '懵懂': 1,
  '青春': 1,
  '提到': 1,
  '朋友': 1,
  '滑块': 26,
  '不困': 1,
  '2022': 1,
  '年': 7,
  '做': 2,
  '几道': 1,
  '01': 1,
  '年算过': 1,
  '经典': 1,
  '莫过于': 1,
  '长板': 7,
  '之间': 5,
  '故事': 3,
  '木板': 1,
  '摩擦': 1,
  '经历': 1,
  '静摩擦': 2,
  '滑动摩擦': 4,
  '过程': 1,
  '题': 1,
  '考察': 1,
  '整体': 2,
  '法': 2,
  '隔离法': 2,
  '外力': 3,
  '两个': 2,
  '物体': 1,
  '静止': 1,
  '加速度': 5,
  '速度': 1,
  '二者之间': 1,
  '静摩擦力': 1,
  '提供': 1,
  '小物块': 2,
  '足够': 1,
  '时': 5,
  '二者': 1,
  '分离': 1,
  '力': 3,
  'a2': 1,
  '大小': 2,
  '增大': 3,
  'a1': 2,
  '不用': 1,
  '斜率': 1,
  '说': 2,
  '忍不住': 2,
  '想': 3,
  '一句'

In [8]:
bm.df #df存储每个词及出现了该词的文档数量

{'前段时间': 11,
 '小伙': 1,
 '花': 31,
 '数万': 4,
 '块': 20,
 '买条': 1,
 '怪鱼': 1,
 '一刀切': 5,
 '开': 35,
 '愣住': 2,
 '鱼肉': 2,
 '蓝色': 5,
 '吃': 44,
 '少见': 4,
 '却是': 21,
 '食用': 7,
 '味道': 16,
 '鱼生': 1,
 '发现': 145,
 '鱼': 4,
 '肉': 3,
 '颜色': 11,
 '粉色': 7,
 '红色': 10,
 '深红色': 1,
 '白色': 9,
 '口感': 5,
 '相差': 9,
 '小编': 2,
 '没到': 5,
 '老婆': 5,
 '孩子': 25,
 '跳': 11,
 '爱': 26,
 '年龄': 17,
 '梦华': 2,
 '录': 7,
 '流泪': 2,
 '懵懂': 1,
 '青春': 5,
 '提到': 62,
 '朋友': 61,
 '滑块': 1,
 '不困': 1,
 '2022': 173,
 '年': 358,
 '做': 196,
 '几道': 2,
 '01': 25,
 '年算过': 1,
 '经典': 28,
 '莫过于': 8,
 '长板': 1,
 '之间': 105,
 '故事': 44,
 '木板': 2,
 '摩擦': 3,
 '经历': 74,
 '静摩擦': 1,
 '滑动摩擦': 1,
 '过程': 74,
 '题': 2,
 '考察': 8,
 '整体': 76,
 '法': 10,
 '隔离法': 1,
 '外力': 4,
 '两个': 116,
 '物体': 7,
 '静止': 2,
 '加速度': 1,
 '速度': 54,
 '二者之间': 1,
 '静摩擦力': 1,
 '提供': 226,
 '小物块': 1,
 '足够': 43,
 '时': 256,
 '二者': 7,
 '分离': 4,
 '力': 13,
 'a2': 1,
 '大小': 19,
 '增大': 6,
 'a1': 1,
 '不用': 30,
 '斜率': 1,
 '说': 254,
 '忍不住': 8,
 '想': 125,
 '一句': 29,
 '选': 21,
 'C': 36,
 '内心': 8,
 '奔': 3,
 

In [9]:
bm.idf #存储每个词的idf值

{'前段时间': 4.083415491689911,
 '小伙': 6.134843129953329,
 '花': 3.04603301202879,
 '数万': 5.031889300457083,
 '块': 3.4920631097060557,
 '买条': 6.134843129953329,
 '怪鱼': 6.134843129953329,
 '一刀切': 4.829767225930285,
 '开': 2.920431824701966,
 '愣住': 5.622572419230658,
 '鱼肉': 5.622572419230658,
 '蓝色': 4.829767225930285,
 '吃': 2.6807136469384596,
 '少见': 5.031889300457083,
 '却是': 3.442949176342377,
 '食用': 4.516703204665761,
 '味道': 3.7150491718473213,
 '鱼生': 6.134843129953329,
 '发现': 1.3270111931037372,
 '鱼': 5.031889300457083,
 '肉': 5.284653004353979,
 '颜色': 4.083415491689911,
 '粉色': 4.516703204665761,
 '红色': 4.175851399000527,
 '深红色': 6.134843129953329,
 '白色': 4.2773968461220075,
 '口感': 4.829767225930285,
 '相差': 4.2773968461220075,
 '小编': 5.622572419230658,
 '没到': 4.829767225930285,
 '老婆': 4.829767225930285,
 '孩子': 3.2663579443776176,
 '跳': 4.083415491689911,
 '爱': 3.226394657282228,
 '年龄': 3.6547315666813738,
 '梦华': 5.622572419230658,
 '录': 4.516703204665761,
 '流泪': 5.622572419230658,
 '懵懂': 6.1

In [11]:
#step 5,优化了流程，这样我们剩下的工作只有输入搜索内容了

def search(sentence):
    corrected,_ = pycorrector.correct(sentence)
    if corrected != sentence:
        c = input("检测到中文输入错误，已自动帮您修改为 ："+corrected+"\n若依然搜索原内容请输入n,否则请输入其他")
        if c != 'n':
            sentence = corrected
    sentence_words = jieba.lcut(sentence)
    tokens = []
    for word in sentence_words:
        if word in stopwords:
            continue
        else:
            tokens.append(word)
    #print(tokens)
    result = bm.score_all(tokens)
    max = result.argsort()[-5:][::-1]
    print("以下是五篇最符合的文章 :",max)
    for i in range(5):
        print("Top",i+1,":",result[max[i]],":",bm.titles[max[i]])
    interact(tokens,max)
    

In [12]:
def interact(tokens,best):
    while True:
        c = input("请选择你你想要阅读的文章(从1到5)，退出请输入q : ")
        if c == 'q':
            break
        else:
            c = int(c)-1
            print('\n' + '-'*20 + '\n' +highlight(tokens,bm.raw_docs[best[c]]) + '\n' + '-'*20 + '\n')
    bm.test_times += 1
    c = input("本次搜索结果的第一位是否符合要求？(y/n)")
    if c == 'y':
        bm.top1 += 1
        bm.top5 += 1
    else:
        c = input("本次搜索结果的前五位是否符合要求？(y/n)")
        if c == 'y':
            bm.top5 += 1
    print("目前精度:")
    print("总次数 :",bm.test_times)
    print("top1 :",bm.top1,"({:0%})".format(bm.top1/bm.test_times))
    print("top5 :",bm.top5,"({:0%})".format(bm.top5/bm.test_times))

    
def highlight(tokens,text):   #高亮搜索文字
    for word in tokens:
        new_word = '\033[031m' + word + '\033[0m'  # red
        len_w = len(word)
        len_t = len(text)
        for i in range(len_t - len_w, -1, -1):
            if text[i: i + len_w] == word:
                text = text[:i] + new_word + text[i + len_w:]
    return text

In [48]:
sentence = input("请输入你要查询的内容 : ")
search(sentence)

请输入你要查询的内容 : 鱼肉是兰色的还能吃吗
检测到中文输入错误，已自动帮您修改为 ：鱼肉是蓝色的还能吃吗
若依然搜索原内容请输入n,否则请输入其他a
以下是五篇最符合的文章 : [  0 510 575 319 318]
Top 1 : 4.506309144614767 : 一刀切下去鱼肉竟是蓝色的，问：还能吃吗，好吃吗？
Top 2 : 0.2372457764493267 : 日本自卫队屡爆多拿食物丑闻，日民众：或因为吃很糟糕的饭，理智被冲昏了
Top 3 : 0.17455036490932535 : 中超球员暴力飞铲对方，赛后道歉：对不起！行胜于言，大家看我的行动
Top 4 : 0.04451659544653037 : 新疆麦趣尔纯牛奶丙二醇添加剂不合格，网友：刚喝完，心态崩了
Top 5 : 0.027647937579409598 : 两批次纯牛奶不合格？麦趣尔回应
请选择你你想要阅读的文章(从1到5)，退出请输入q : q
本次搜索结果的第一位是否符合要求？(y/n)y
目前精度:
总次数 : 560
top1 : 399 (71.250000%)
top5 : 479 (85.535714%)
